In [1]:
import numpy as np
from scipy.optimize import fsolve, root, root_scalar
import scipy.optimize as opt

Solving equations in $\mathbb{R}$
===

Given $f: \mathbb{R} \rightarrow \mathbb{R},$ find $x^*\in\mathbb{R}$ such that $f(x^*) = 0.$ 

1. Bisection method
---

In [2]:
def bisection(f, a, b, epsi=1e-8, tol=1e-6):
    # A simple implementation of the bisection method.
    # f: a function of x
    # a, b: a bracket for f
    # epsi: error for x*
    # tol: error for f(x*)

    if a >= b:
        raise RuntimeError('a must be smaller than b')
        
    x0, x1 = a, b  # start with the provided bracket
    y0, y1 = f(x0), f(x1)

    if np.isclose(y0, 0.0):
        return x0 # that's the solution
    if np.isclose(y1, 0.0):
        return x1
        
    if y0 * y1 > 0:
        raise RuntimeError('a, b must satisfy f(a)f(b) < 0')

    err = 1.0
    while (err > tol) and (np.abs(x1 - x0) > epsi):
        x2 = 0.5 * (x0 + x1)
        y2 = f(x2)

        if np.isclose(y2, 0.0):
            # just found the solution
            return x2
            
        if y2 * y0 < 0:
            x1, y1 = x2, y2
        else:
            x0, y0 = x2, y2
        err = np.abs(y2)

    return x2

In [3]:
# Solution to x^2 - x - 2 = 0:
fx = lambda x: x**2 - x - 2
print(bisection(fx, 1, 3))

2.0


In [4]:
# Recursive implementation - not ideal for

def bisection_recursive(f, a, b, epsi=1e-8, tol=1e-6): 
    if a >= b:
        raise RuntimeError('a must be smaller than b')
        
    x0, x1 = a, b  # start with the provided bracket
    y0, y1 = f(x0), f(x1)

    if np.isclose(y0, 0.0):
        return x0 # that's the solution
    if np.isclose(y1, 0.0):
        return x1
        
    if y0 * y1 > 0:
        raise RuntimeError('a, b must satisfy f(a)f(b) < 0')

    x2 = 0.5 * (x0 + x1)
    y2 = f(x2)

    err = np.abs(y2)
    if (err <= tol) or (np.abs(x1 - x0) <= epsi):
        # stopping condition
        return x2
        
    if y2 * y0 < 0:
        return bisection_recursive(f, x0, x2)
    else:
        return bisection_recursive(f, x2, x1)

In [5]:
bisection_recursive(fx, 0, 5)

1.9999998807907104

2. Newton-Raphson iterative method
---

In [6]:
def NR_iter(f, fprime, x, tol=1e-8, max_iter=100):
    # f: function
    # fprime: differential of f
    # x: initial approximation
    # tol: tolerance
    # max_iter: maximum number of iterations

    xk = np.zeros((max_iter,), dtype=np.float64)  # successive approximations, trace
    xk[0] = x

    k = 1
    while k < max_iter:
        # step: x <- x - f(x) / fprime(x)
        xk[k] = xk[k-1] - f(xk[k-1]) / fprime(xk[k-1])
        if np.abs(f(xk[k]) - f(xk[k-1])) < tol:
            break
        k = k + 1
    if k >= max_iter:
        print('Warning: The method did not converge!')
    return xk[k], xk[:k]   # return solution and trace 

In [7]:
f = lambda x: x**2 - 4*np.sin(x)
fprime = lambda x: 2*x - 4*np.cos(x)

In [8]:
NR_iter(f, fprime, 3)

(1.9337537628270212,
 array([3.        , 2.15305769, 1.95403864, 1.93397153, 1.93375379,
        1.93375376]))

3. Secant method
---

In [9]:
def secant(f, x0, x1, tol=1e-6, max_iter=100):
    # f: function
    # x0, x1: initial approximations
    # tol: tolerance
    # max_iter: maximum number of iterations

    xk = np.zeros((max_iter+1,), dtype=np.float64)
    xk[0:2] = (x0, x1)

    k = 1
    while k < max_iter:
        y0, y1 = f(xk[k-1]), f(xk[k])
        d =  y1 - y0
        if np.abs(d) < tol:
            break
            
        xk[k+1] = (xk[k-1] * y1 - xk[k] * y0) / d
        y2 = f(xk[k+1])
        
        if np.abs(y2 - y1) < tol:
            break
        
        k += 1
        
    if k >= max_iter:
        print('Warning: The method did not converge!')

    return xk[k], xk[:k]

In [10]:
secant(f, 1.5, 2)

(1.9337537599018961,
 array([1.5       , 2.        , 1.91373122, 1.93305421, 1.93376146]))

Exercise -- optimization
===

Design the optimal beer can! It must be:

- cylindrical
- ecological: uses the minimum amount of materials (i.e. minimum total surface)
- of exact volume $V=333 cm^3$
- not higher than twice its diameter

Tasks:
- identify the variables
- write the mathematical formulation of the problem
- write the formula of the gradient of the objective function and the Jacobian of the nonlinear constraint function
- implement the solution

**Solution**
---

- variables: $x_0$ the diameter, $x_1$ the height of the can
- Problem: let $\mathbf{x} = [x_0, x_0]^T$
 
$$
\text{minimize}\quad f(\mathbf{x}) = \frac{\pi x_0^2}{2} + \pi x_0 x_1
\quad\text{with respect to $x_0, x_1$}
$$
subject to
\begin{gather*}
-2 x_0 + x_1 \leq 0 \\
c_{eq}(\mathbf{x}) = 333 - \frac{\pi x_0^2}{4}x_1 = 0
\end{gather*}

The differentials:

- the gradient of the objective function:
$$ 
\nabla f(\mathbf{x}) = 
\left[
\frac{\partial f}{\partial x_0}, \frac{\partial f}{\partial x_1}
\right]^T
= [\pi(x_0 + x_1), \pi x_0]^T
$$

- the Jacobian of the nonlinear constraint function
(which is a scalar function, so it's a gradient finally):
$$
\mathbf{J}_{c_{eq}} = \left[
\frac{\partial c_{eq}}{\partial x_0}, \frac{\partial c_{eq}}{\partial x_1}
\right]
=
\left [
-\frac{\pi}{2}x_0 x_1, -\frac{\pi}{4}x_0^2
\right ]
$$


In [11]:
from scipy.optimize import Bounds, LinearConstraint, NonlinearConstraint

In [12]:
f = lambda x: np.pi*x[0]*x[1] + 0.5*np.pi*x[0]**2 # x[0] - diameter, x[1] - height
f_J = lambda x: np.array([np.pi*(x[0]+x[1]), np.pi*x[0]])

In [13]:
# check the documentation!!!
bounds = Bounds([4.0, 5.0], [5.0, 15.0])
lconstr = LinearConstraint([-2.0, 1.0], [-np.inf], [0.0])

In [14]:
# non-linear constraint:
nl_f = lambda x: 333 - 0.25 * np.pi*x[0]**2 * x[1]  # 333 is the target volume

# Jacobian of the non-linear constraint
nl_J = lambda x: np.array([-0.5*np.pi*x[0]*x[1], -0.25*np.pi*x[0]**2])

# Hessian of the non-linear constraint
nl_H = lambda x, v: v[0] * np.array([[-0.5*np.pi*x[1], -0.5*np.pi*x[0]],[-0.5*np.pi*x[0],0]])

nl_constr = NonlinearConstraint(nl_f, 0, 0,  # 0 <= nl_f <= 0 -> nl_f = 0 
                                jac=nl_J, hess=nl_H)

In [15]:
res = opt.minimize(f, 
                   np.array([5.0, 5.0]),  # some initial guess
                   method='trust-constr',
                   jac=f_J,
                   hess='3-point',
                   constraints=[lconstr, nl_constr],
                   bounds=bounds,
                   options={'verbose': 1})

`xtol` termination condition is satisfied.
Number of iterations: 400, function evaluations: 376, CG iterations: 388, optimality: 4.33e-15, constraint violation: 9.37e-01, execution time: 0.24 s.


/home/vlad/.cache/pypoetry/virtualenvs/e7441-9Dg15fjw-py3.11/lib/python3.11/site-packages/scipy/optimize/_trustregion_constr/equality_constrained_sqp.py:203: UserWarning: Singular Jacobian matrix. Using SVD decomposition to perform the factorizations.
  Z, LS, Y = projections(A, factorization_method)
/home/vlad/.cache/pypoetry/virtualenvs/e7441-9Dg15fjw-py3.11/lib/python3.11/site-packages/scipy/optimize/_trustregion_constr/equality_constrained_sqp.py:80: UserWarning: Singular Jacobian matrix. Using SVD decomposition to perform the factorizations.
  Z, LS, Y = projections(A, factorization_method)


In [16]:
print(res)

           message: `xtol` termination condition is satisfied.
           success: True
            status: 2
               fun: 279.7202087123787
                 x: [ 5.937e+00  1.203e+01]
               nit: 400
              nfev: 376
              njev: 2657
              nhev: 0
          cg_niter: 388
      cg_stop_cond: 2
              grad: [ 5.644e+01  1.865e+01]
   lagrangian_grad: [ 4.330e-15  1.965e-15]
            constr: [array([ 1.548e-01]), array([ 5.592e-03]), array([ 5.937e+00,  1.203e+01])]
               jac: [array([[-2.000e+00,  1.000e+00]]), array([[-1.122e+02, -2.768e+01]]), array([[ 1.000e+00,  0.000e+00],
                           [ 0.000e+00,  1.000e+00]])]
       constr_nfev: [0, 376, 0]
       constr_njev: [0, 125, 0]
       constr_nhev: [0, 127, 0]
                 v: [array([-3.079e+00]), array([ 5.625e-01]), array([ 5.053e-01,  3.979e-10])]
            method: tr_interior_point
        optimality: 4.3298697960381105e-15
  constr_violation: 0.936955008